In [ ]:
import numpy as np
import matplotlib
import matplotlib.pyplot as plt
plt.style.use('classic')

In [ ]:
#Evolution algorithms for ordinary differential equations

In [ ]:
#Kepler problem functions

lam = 1.0  #  λ parameter

# Potential
def V(x, y):
    return -lam / np.sqrt(x**2 + y**2)

# x direction Kernel
def Kx(x, y):
    return -lam * x / (x**2 + y**2)**1.5

# y direction kernel
def Ky(x, y):
    return -lam * y / (x**2 + y**2)**1.5

# Hamiltonian/Energy
def H(x, y, px, py):
    return 0.5 * (px**2 + py**2) + V(x, y)

# Angular momentum
def L(x, y, px, py):
    return x * py - y * px

In [ ]:
#Intial conditions (ICs)

#Some ICs we want to have an ellipse (give negative Energy, nonzero Angular Momentum -> negative eccentrity)
x0 = 0.5
y0 = 0.0
px0 = 0.0
py0 = 1.0

# Function to set the above values to the variables
def set_initial_conditions(x, y, px, py):
    px[0] = px0
    py[0] = py0
    x[0] = x0
    y[0] = y0


In [ ]:
#Analytical solutions for comparison

# Initial energy and angular momentum (constant)
En0 = H(x0, y0, px0, py0)
L0  = L(x0, y0, px0, py0)

# Eccentrity function
def ecc(Lval, Eval):
    return np.sqrt(1.0 + 2.0 * Eval * Lval**2)

# Helper function
def ellipse(theta, e):
    return 1.0 / (1.0 + e * np.cos(theta))

# Solution in polar coordinates
def r_theta(theta, Lval, Eval):
    return -Lval**2 * ellipse(theta, ecc(Lval, Eval))


ang = np.arange(0.0, 2.0 * np.pi, 0.01) #array of angles in a revolution
rAn = r_theta(ang, L0, En0) #corresponding radial position for the chosen ICs
# Analytical solution in cartesian coordinates
xAn = rAn * np.cos(ang)
yAn = rAn * np.sin(ang)

In [ ]:
#Some time amount for which we will solve  using different time integrators
t_max = 10.0

In [ ]:
# 1-Forward-Euler (FE) integrator

In [ ]:
# FE integrator for some IC and dt
def forward_euler(x, y, px, py, dt):
    nSteps = len(x) # Note that 
    for i in range(nSteps - 1):
        px[i+1] = px[i] + dt * Kx(x[i], y[i])
        py[i+1] = py[i] + dt * Ky(x[i], y[i])
        x[i+1] = x[i] + dt * px[i]
        y[i+1] = y[i] + dt * py[i]


In [ ]:
# Solution for a particular dt

dtFE = 0.003
nStepsFE = int(round(t_max / dtFE)) #Number of steps for the selected tmax and dt

#Position and conjugate momenta arrays for each time step
xFE = np.zeros(nStepsFE); yFE = np.zeros(nStepsFE)
pxFE = np.zeros(nStepsFE); pyFE = np.zeros(nStepsFE)

# Set ICs and solve for FE integrator
set_initial_conditions(xFE, yFE, pxFE, pyFE)
forward_euler(xFE, yFE, pxFE, pyFE, dtFE)
tsFE = np.arange(1, nStepsFE + 1) * dtFE #Time array

In [ ]:
#Comparison of the trayectory during tmax
plt.figure()
plt.plot(xFE, yFE, label='Forward-Euler')
plt.plot(xAn, yAn, 'k--', label='Analytical')
plt.axis('equal'); plt.xlabel(r"$x$",fontsize=20); plt.ylabel(r"$y$",fontsize=20)
plt.title("Trayectory in Forward-Euler"); plt.legend()



In [ ]:
#Evolution of the energy for FE
enFE = H(xFE, yFE, pxFE, pyFE) #Compute energy with hamiltonian function

plt.figure()
plt.plot(tsFE, enFE)
plt.xlabel(r"$t$",fontsize=20); plt.ylabel("Energy",fontsize=18)
plt.title(f"Energy in Forward-Euler")

In [ ]:
#Phase space for FE
plt.figure()
plt.plot(xFE, pxFE)
plt.xlabel(r"$x$",fontsize=20); plt.ylabel(r"$p_x$",fontsize=20)
plt.title("Phase Space in Forward Euler")

In [ ]:
#Angular momentum for FE
LFE = L(xFE, yFE, pxFE, pyFE)#Compute angular momentum with the function

plt.figure()
plt.plot(tsFE, LFE)
plt.xlabel(r"$t$",fontsize=20); plt.ylabel("Angular momentum",fontsize=18)
plt.title("Angular Momentum in-Forward Euler")

In [ ]:
# 2 Semi-implicit Euler (SE) integrator

In [ ]:
# SE integrator for some IC and dt

def semi_implicit_euler(x, y, px, py, dt):
    nSteps = len(x)
    for i in range(nSteps - 1):
        px[i+1] = px[i] + dt * Kx(x[i], y[i])
        py[i+1] = py[i] + dt * Ky(x[i], y[i])
        x[i+1] = x[i] + dt * px[i+1]
        y[i+1] = y[i] + dt * py[i+1]

In [ ]:
# Solution for a particular dt
dtSE = 0.003
nStepsSE = int(round(t_max / dtSE))#Number of steps for the selected tmax and dt

#Position and conjugate momenta arrays for each time step
xSE = np.zeros(nStepsSE); ySE = np.zeros(nStepsSE)
pxSE = np.zeros(nStepsSE); pySE = np.zeros(nStepsSE)


# Set ICs and solve for FE integrator
set_initial_conditions(xSE, ySE, pxSE, pySE)
semi_implicit_euler(xSE, ySE, pxSE, pySE, dtSE)
tsSE = np.arange(1, nStepsSE + 1) * dtSE #Time array

In [ ]:
#Angular momentum for SE
LSE  = L(xSE, ySE, pxSE, pySE)#Compute angular momentum with the function

plt.figure()
plt.plot(tsSE, LSE)
plt.xlabel(r"$t$",fontsize=20); plt.ylabel("Angular momentum",fontsize=18),plt.ylim(0.4,0.6)
plt.title("Angular Momentum in Semi-implicit Euler")

In [ ]:
#Angular momentum for SE, relative difference with IC value

plt.figure()
plt.plot(tsSE, abs((LSE-LSE[1])/LSE[1]))
plt.xlabel(r"$t$",fontsize=20); plt.ylabel(r"$\Delta L$",fontsize=18)
plt.title("Angular Momentum in Semi-implicit Euler")

In [ ]:
#Comparison of the trayectory during tmax
plt.figure()
plt.plot(xSE, ySE, label='Semi-implicit Euler')
plt.plot(xAn, yAn, 'k--', label='Analytical')
plt.axis('equal'); plt.xlabel(r"$x$", fontsize=20); plt.ylabel(r"$y$",fontsize=20)
plt.title(f"Trayectory in Semi-implicit Euler"); plt.legend()


In [ ]:
#Evolution of the energy for SE
enSE = H(xSE, ySE, pxSE, pySE) #Compute energy with hamiltonian function

plt.figure()
plt.plot(tsSE, enSE)
plt.xlabel(r"$t$",fontsize=20); plt.ylabel("Energy",fontsize=18)
plt.title(f"Energy in Semiimplicit Euler")

In [ ]:
#Phase space for SE
plt.figure()
plt.plot(xSE, pxSE)
plt.xlabel(r"$x$",fontsize=20); plt.ylabel(r"$p_x$",fontsize=20),plt.ylim(-2.5,2.5)
plt.title("Phase Space in Semi-Implicit Euler")

In [ ]:
# Solution for dt/2 in SE
xSE2 = np.zeros(2*nStepsSE); ySE2 = np.zeros(2*nStepsSE)
pxSE2 = np.zeros(2*nStepsSE); pySE2 = np.zeros(2*nStepsSE)

#Position and conjugate momenta arrays for each dt/2 time step
set_initial_conditions(xSE2, ySE2, pxSE2, pySE2)
semi_implicit_euler(xSE2, ySE2, pxSE2, pySE2, dtSE/2.)
tsSE2 = np.arange(1, 2*nStepsSE + 1) * dtSE/2.

In [ ]:
# Comparison of the evolution of the energy in SE for dt and dt/2
enSE2 = H(xSE2, ySE2, pxSE2, pySE2) #Compute energy with hamiltonian function for dt/2 case

plt.figure()
plt.plot(tsSE, enSE, label=f"Semi-implicit Euler dt={dtSE}")
plt.plot(tsSE2, enSE2, 'k--', label=f"Semi-implicit Euler dt={dtSE/2.}")
plt.xlabel(r"$t$",fontsize=20); plt.ylabel("Energy",fontsize=18),plt.legend()
plt.title(f"Energy comparison in Semi-implicit Euler")

In [ ]:
# Comparison of the energy conservation in SE for dt and dt/2

plt.figure()
plt.plot(tsSE, abs((enSE-enSE[1])/enSE[1]), label=f"Semi-implicit Euler dt={dtSE}")
plt.plot(tsSE2, abs((enSE2-enSE2[1])/enSE2[1]), 'k--', label=f"Semi-implicit Euler dt={dtSE/2.}")
plt.xlabel(r"$t$", fontsize=20); plt.ylabel(r"$\Delta E$", fontsize=20),plt.yscale("log")
plt.title("Energy conservation comparison in Semi-implicit Euler"); plt.legend(loc='lower right')


In [ ]:
# SE integrator-order using 10 samples with decreasing dt

dt = 0.01 #Biggest time step
nSample = 10 #number of time step options

dts = np.zeros(nSample) #array with the dt of each sample
enCFE = np.zeros(nSample) #array with the maximun gap respect to the exact energy for each sample

for n in range(1, nSample+1):
    nSteps = n * nStepsSE # nStepSE is just an integer, 3333 in this case. It only sets tmax.
    
    x = np.zeros(nSteps)
    y = np.zeros(nSteps)
    px = np.zeros(nSteps)
    py = np.zeros(nSteps)

    #IC and SE solution for the nth sample
    set_initial_conditions(x, y, px, py)
    semi_implicit_euler(x, y, px, py, dt/n)


    dts[n-1] = dt / n #store the dt of the sample in an array
    en = H(x, y, px, py) #get the energy
    enCFE[n-1] = np.max(np.abs((en - en[0]) / en[0])) #store the maximun gap respect to the expected constant value



In [ ]:
# O(dt^l) dependance using the energy conservation gap, for SE l=1
plt.figure()
plt.scatter(dts, enCFE)
plt.xlabel(r"$dt$",fontsize=20)
plt.ylabel(r"$\max(\Delta E)$",fontsize=20)
plt.title(r"$\mathcal{O}(dt^l) \ $"+"of Semi-Implicit Euler", fontsize=20)
plt.show()

In [ ]:
# Velocity-Verlet integrator for some IC and dt
def velocity_verlet(x, y, px, py, dt):
    nSteps = len(x)
    for i in range(nSteps - 1):
        px_half = px[i] + 0.5 * dt * Kx(x[i], y[i])
        py_half = py[i] + 0.5 * dt * Ky(x[i], y[i])
        x[i+1] = x[i] + dt * px_half
        y[i+1] = y[i] + dt * py_half
        px[i+1] = px_half + 0.5 * dt * Kx(x[i+1], y[i+1])
        py[i+1] = py_half + 0.5 * dt * Ky(x[i+1], y[i+1])


# Position-Verlet integrator for some IC and dt
def position_verlet(x, y, px, py, dt):
    nSteps = len(x)
    for i in range(nSteps - 1):
        x_mid = x[i] + 0.5 * dt * px[i]
        y_mid = y[i] + 0.5 * dt * py[i]
        px[i+1] = px[i] + dt * Kx(x_mid, y_mid)
        py[i+1] = py[i] + dt * Ky(x_mid, y_mid)
        x[i+1] = x_mid + 0.5 * dt * px[i+1]
        y[i+1] = y_mid + 0.5 * dt * py[i+1]

In [ ]:
# Solution for a particular dt
dtVV = 0.003
dtPV = 0.003
nStepsVV = int(round(t_max / dtVV))#Number of steps for the selected tmax and dt

#Position and conjugate momenta arrays for each time step in VV
xVV = np.zeros(nStepsVV); yVV = np.zeros(nStepsVV)
pxVV = np.zeros(nStepsVV); pyVV = np.zeros(nStepsVV)

#Position and conjugate momenta arrays for each time step in PV
xPV = np.zeros(nStepsVV); yPV = np.zeros(nStepsVV)
pxPV = np.zeros(nStepsVV); pyPV = np.zeros(nStepsVV)

# Set ICs and solve for FE integrator
set_initial_conditions(xVV, yVV, pxVV, pyVV)
velocity_verlet(xVV, yVV, pxVV, pyVV, dtVV)  
set_initial_conditions(xPV, yPV, pxPV, pyPV)
position_verlet(xPV, yPV, pxPV, pyPV, dtPV) 
tsVV = np.arange(1, nStepsVV + 1) * dtVV #Time array


In [ ]:
#Comparison of the trayectory during tmax
plt.figure()
plt.plot(xVV, yVV, label='Velocity-Verlet')
plt.plot(xAn, yAn, 'k--', label='Analytical')
plt.axis('equal'); plt.xlabel(r"$x$", fontsize=20); plt.ylabel(r"$y$",fontsize=20)
plt.title(f"Trayectory in Velocity-Verlet"); plt.legend()

In [ ]:
#Comparison of the trayectory during tmax
plt.figure()
plt.plot(xPV, yPV, label='Position-Verlet')
plt.plot(xAn, yAn, 'k--', label='Analytical')
plt.axis('equal'); plt.xlabel(r"$x$", fontsize=20); plt.ylabel(r"$y$",fontsize=20)
plt.title(f"Trayectory in Position-Verlet"); plt.legend()

In [ ]:
# VV and PV integrator-order using 10 samples with decreasing dt

dt = 0.01 #Biggest time step
nSample = 10 #number of time step options

dts = np.zeros(nSample) #array with the dt of each sample
enCVV = np.zeros(nSample) #VV array with the maximun gap respect to the exact energy for each sample
enCPV = np.zeros(nSample) #PV array with the maximun gap respect to the exact energy for each sample

for n in range(1, nSample+1):
    nSteps = n * nStepsSE  # nStepSE is just an integer, 3333 in this case. It only sets tmax. 
    dts[n-1] = dt / n #store the dt of the sample in an array
    
    
    # VV integrator arrays
    x1 = np.zeros(nSteps)
    y1= np.zeros(nSteps)
    px1 = np.zeros(nSteps)
    py1 = np.zeros(nSteps)

    #IC and VV solution for the nth sample
    set_initial_conditions(x1, y1, px1, py1)
    velocity_verlet(x1, y1, px1, py1, dt/n)

    en1 = H(x1, y1, px1, py1) #get the energy 
    enCVV[n-1] = np.max(np.abs((en1 - en1[0]) / en1[0])) #store the maximun gap respect to the expected constant value


    # PV integrator arrays
    x2 = np.zeros(nSteps)
    y2= np.zeros(nSteps)
    px2 = np.zeros(nSteps)
    py2 = np.zeros(nSteps)

    #IC and PV solution for the nth sample
    set_initial_conditions(x2, y2, px2, py2)
    position_verlet(x2, y2, px2, py2, dt/n)

    
    en2 = H(x2, y2, px2, py2) #get the energy 
    enCPV[n-1] = np.max(np.abs((en2 - en2[0]) / en2[0])) #store the maximun gap respect to the expected constant value




In [ ]:
# O(dt^l) dependance using the energy conservation gap, for SE, VV ad PV
plt.figure()
plt.scatter(dts, enCFE,label="Semi-Implicit Euler",c='blue')
plt.plot(dts,7*dts,c="blue", label=r"$\propto dt$")
plt.scatter(dts, enCVV,label="Velocity-Verlet",c='red')
plt.plot(dts,72*dts**2,c="red", label=r"$\propto dt^2$")
plt.scatter(dts, enCPV,label="Position-Verlet",c='green')
plt.plot(dts,19*dts**2,c="green", label=r"$\propto dt^2$")

plt.xscale("log")
plt.yscale("log")
plt.xlabel(r"$dt$",fontsize=20)
plt.ylabel(r"$\max(\Delta E)$",fontsize=20)
plt.title(r"$\mathcal{O}(dt^l) \ $"+"of different integrators", fontsize=20)
plt.ylim(1e-6,3e-1)
plt.xlim(5e-4,3e-2)
plt.legend(loc='lower right')
plt.show()

In [ ]:
# gráfico
plt.figure()
plt.scatter(dts, enCVV)
plt.plot(dts, 72*dts**2)
plt.scatter(dts, enCPV)
plt.plot(dts, 19*dts**2)
plt.scatter(dts, enCFE)
plt.plot(dts, 7*dts)
plt.xscale("log")
plt.yscale("log")
plt.xlabel("dt")
plt.ylabel(r"$\max(\Delta E)$")
plt.title("Energy conservation")
plt.show()